Data Ingestion

In [ ]:
from langchain_core.documents import Document

In [ ]:
doc=Document(
    page_content="This is a main RAG document.",
    metadata={
        "source": "myfile.txt",
        "pages": 1,
        "author": "Vidhi Sinha",
        "date_created": "2026-01-16"    
     }        

)
doc

Document(metadata={'source': 'myfile.txt', 'pages': 1, 'author': 'Vidhi Sinha', 'date_created': '2026-01-16'}, page_content='This is a main RAG document.')

<h1>RAG Pipelines - Data Ingestion to Vector DB Pipeline</h1>

In [10]:
import langchain_core.runnables
print("Import successful!")

import os
from pathlib import Path
from langchain_community.document_loaders import PyPDFLoader
from langchain_text_splitters import RecursiveCharacterTextSplitter

Import successful!



In [11]:
import sys
print(sys.executable)
print(sys.path)


c:\Users\vidhi\AppData\Local\Programs\Python\Python313\python.exe
['c:\\Users\\vidhi\\AppData\\Local\\Programs\\Python\\Python313\\python313.zip', 'c:\\Users\\vidhi\\AppData\\Local\\Programs\\Python\\Python313\\DLLs', 'c:\\Users\\vidhi\\AppData\\Local\\Programs\\Python\\Python313\\Lib', 'c:\\Users\\vidhi\\AppData\\Local\\Programs\\Python\\Python313', '', 'C:\\Users\\vidhi\\AppData\\Roaming\\Python\\Python313\\site-packages', 'c:\\Users\\vidhi\\AppData\\Local\\Programs\\Python\\Python313\\Lib\\site-packages', 'c:\\Users\\vidhi\\AppData\\Local\\Programs\\Python\\Python313\\Lib\\site-packages\\win32', 'c:\\Users\\vidhi\\AppData\\Local\\Programs\\Python\\Python313\\Lib\\site-packages\\win32\\lib', 'c:\\Users\\vidhi\\AppData\\Local\\Programs\\Python\\Python313\\Lib\\site-packages\\Pythonwin']


In [12]:
import langchain_core.runnables
print("Import successful!")


Import successful!


In [13]:
### Read all pdfs in a directory
def process_all_pdfs(pdf_directory):
    all_documents = []
    pdf_dir = Path(pdf_directory)   

    pdf_files = list(pdf_dir.glob("**/*.pdf"))

    print(f'Found {len(pdf_files)} PDF files to process')

    for pdf_file in pdf_files:  
        print(f'\nProcessing file: {pdf_file.name}')

        try:
            loader = PyPDFLoader(str(pdf_file))
            documents = loader.load()

            for doc in documents:
                doc.metadata['source_file'] = pdf_file.name
                doc.metadata['file_type'] = 'pdf' 

            all_documents.extend(documents)
            print(f'Loaded {len(documents)} pages')
        
        except Exception as e:
            print(f'Error loading {pdf_file}: {e}') 

    print(f'\nTotal documents loaded: {len(all_documents)}')
    return all_documents

all_pdf_documents = process_all_pdfs("../data")    

            

Found 4 PDF files to process

Processing file: Business_Finance.pdf
Loaded 64 pages

Processing file: Finance_Bill.pdf
Loaded 188 pages

Processing file: Finance_detail.pdf
Loaded 195 pages

Processing file: PrinciplesofFinance.pdf
Loaded 643 pages

Total documents loaded: 1090


In [14]:
all_pdf_documents

[Document(metadata={'producer': 'Microsoft® Word for Office 365', 'creator': 'Microsoft® Word for Office 365', 'creationdate': '2019-02-03T11:33:09+05:30', 'title': 'Unit I (Business Environment)', 'author': 'erstudy Classs', 'moddate': '2019-02-03T11:33:09+05:30', 'source': '..\\data\\pdf\\Business_Finance.pdf', 'total_pages': 64, 'page': 0, 'page_label': '1', 'source_file': 'Business_Finance.pdf', 'file_type': 'pdf'}, page_content='UNIT SNAPSHOT   \nUGC NET COMMERCE \nUnit 4 \nBusiness Finance'),
 Document(metadata={'producer': 'Microsoft® Word for Office 365', 'creator': 'Microsoft® Word for Office 365', 'creationdate': '2019-02-03T11:33:09+05:30', 'title': 'Unit I (Business Environment)', 'author': 'erstudy Classs', 'moddate': '2019-02-03T11:33:09+05:30', 'source': '..\\data\\pdf\\Business_Finance.pdf', 'total_pages': 64, 'page': 1, 'page_label': '2', 'source_file': 'Business_Finance.pdf', 'file_type': 'pdf'}, page_content='www.everstudy.co.in  Query: everstudyclasses@gmail.com \n❖

In [15]:
def split_documents(documents, chunk_size=1000, chunk_overlap=200):
    text_splitter = RecursiveCharacterTextSplitter(
        chunk_size=chunk_size,
        chunk_overlap=chunk_overlap,
        length_function=len,
        separators=["\n\n", "\n", " ", ""]
    )

    split_docs = text_splitter.split_documents(documents)
    print(f'Split {len(documents)} documents into {len(split_docs)} chunks')
    
    if split_docs:
        print(f'\nExample chunk:')
        print(f'Content: {split_docs[0].page_content[:200]}...')
        print(f'METADATA: {split_docs[0].metadata}')

    return split_docs   

In [16]:
from langchain_core.documents import Document

chunks = split_documents(all_pdf_documents)
chunks

Split 1090 documents into 3139 chunks

Example chunk:
Content: UNIT SNAPSHOT   
UGC NET COMMERCE 
Unit 4 
Business Finance...
METADATA: {'producer': 'Microsoft® Word for Office 365', 'creator': 'Microsoft® Word for Office 365', 'creationdate': '2019-02-03T11:33:09+05:30', 'title': 'Unit I (Business Environment)', 'author': 'erstudy Classs', 'moddate': '2019-02-03T11:33:09+05:30', 'source': '..\\data\\pdf\\Business_Finance.pdf', 'total_pages': 64, 'page': 0, 'page_label': '1', 'source_file': 'Business_Finance.pdf', 'file_type': 'pdf'}


[Document(metadata={'producer': 'Microsoft® Word for Office 365', 'creator': 'Microsoft® Word for Office 365', 'creationdate': '2019-02-03T11:33:09+05:30', 'title': 'Unit I (Business Environment)', 'author': 'erstudy Classs', 'moddate': '2019-02-03T11:33:09+05:30', 'source': '..\\data\\pdf\\Business_Finance.pdf', 'total_pages': 64, 'page': 0, 'page_label': '1', 'source_file': 'Business_Finance.pdf', 'file_type': 'pdf'}, page_content='UNIT SNAPSHOT   \nUGC NET COMMERCE \nUnit 4 \nBusiness Finance'),
 Document(metadata={'producer': 'Microsoft® Word for Office 365', 'creator': 'Microsoft® Word for Office 365', 'creationdate': '2019-02-03T11:33:09+05:30', 'title': 'Unit I (Business Environment)', 'author': 'erstudy Classs', 'moddate': '2019-02-03T11:33:09+05:30', 'source': '..\\data\\pdf\\Business_Finance.pdf', 'total_pages': 64, 'page': 1, 'page_label': '2', 'source_file': 'Business_Finance.pdf', 'file_type': 'pdf'}, page_content='www.everstudy.co.in  Query: everstudyclasses@gmail.com \n❖

In [17]:
!pip install chromadb

### Embeddings

In [18]:

import numpy as np
from sentence_transformers import SentenceTransformer   
import chromadb
from chromadb.config import Settings 
import uuid
from typing import List, Dict, Any, Tuple
from sklearn.metrics.pairwise import cosine_similarity


In [19]:
class EmbeddingManager:
    def __init__(self, model_name: str = 'all-MiniLM-L6-v2'):
        self.model_name = model_name
        self.model = None
        self.load_model()

    def load_model(self):

        try:
            print(f'Loading embedding model: {self.model_name}')
            self.model = SentenceTransformer(self.model_name)
            print(f'Model loaded successfully. Embedding dimension: {self.model.get_sentence_embedding_dimension()} ')
        except Exception as e:
            print(f"Error loading model: {e}")  
            raise

    def generate_embedding(self, texts: List[str]) -> np.ndarray:
        if not self.model:
             raise ValueError("Model not loaded.")
        print(f'Generating embeddings for {len(texts)} texts')
        embeddings = self.model.encode(texts, convert_to_numpy=True)
        return embeddings  

embedding_manager = EmbeddingManager()

Loading embedding model: all-MiniLM-L6-v2
Model loaded successfully. Embedding dimension: 384 


In [20]:
embedding_manager 

### VectorStore

In [21]:
import os

class VectorStore:
    def __init__(self, collection_name: str = "pdf_documents", persist_directory: str = "../data/vector_store"):
        
        self.collection_name = collection_name
        self.persist_directory = persist_directory
        self.client = None
        self.collection = None
        self.initialize_vector_store()
        

    def initialize_vector_store(self):
        try:
            os.makedirs(self.persist_directory, exist_ok=True)
            self.client = chromadb.PersistentClient(path=self.persist_directory)
            self.collection = self.client.get_or_create_collection(name=self.collection_name)
            print(f'Initialized vector store with collection: {self.collection_name}')
            print(f'Existing documents in collection: {self.collection.count()}')

        except Exception as e:  
            print(f"Error initializing vector store: {e}")  
            raise
    
    def add_documents(self, documents: List[Any], embeddings: np.ndarray):
        if len(documents) != len(embeddings):
            raise ValueError("Number of documents and embeddings must match.")
        
        print(f'Added {len(documents)} documents to vector store. Total now: {self.collection.count()}')    
    
        ids = []
        metadatas = []
        documents_texts = []
        embeddings_list = []

        for i, doc in enumerate(documents):

            doc_id = f"doc_{uuid.uuid4().hex[:8]}_{i}"
            ids.append(doc_id)
            metadata = dict(doc.metadata)
            metadata['content_length'] = len(doc.page_content)
            metadatas.append(metadata)
            documents_texts.append(doc.page_content)
            embeddings_list.append(embeddings[i].tolist())

        try:
            self.collection.add(
                ids=ids,
                metadatas=metadatas,
                documents=documents_texts,
                embeddings=embeddings_list
            )
            print(f'Successfully added {len(documents)} documents to vector store. Total now: {self.collection.count()}')
        except Exception as e:
            print(f"Error adding documents to vector store: {e}")  
            raise
vectorstore = VectorStore()
vectorstore







Initialized vector store with collection: pdf_documents
Existing documents in collection: 0


In [22]:
chunks

[Document(metadata={'producer': 'Microsoft® Word for Office 365', 'creator': 'Microsoft® Word for Office 365', 'creationdate': '2019-02-03T11:33:09+05:30', 'title': 'Unit I (Business Environment)', 'author': 'erstudy Classs', 'moddate': '2019-02-03T11:33:09+05:30', 'source': '..\\data\\pdf\\Business_Finance.pdf', 'total_pages': 64, 'page': 0, 'page_label': '1', 'source_file': 'Business_Finance.pdf', 'file_type': 'pdf'}, page_content='UNIT SNAPSHOT   \nUGC NET COMMERCE \nUnit 4 \nBusiness Finance'),
 Document(metadata={'producer': 'Microsoft® Word for Office 365', 'creator': 'Microsoft® Word for Office 365', 'creationdate': '2019-02-03T11:33:09+05:30', 'title': 'Unit I (Business Environment)', 'author': 'erstudy Classs', 'moddate': '2019-02-03T11:33:09+05:30', 'source': '..\\data\\pdf\\Business_Finance.pdf', 'total_pages': 64, 'page': 1, 'page_label': '2', 'source_file': 'Business_Finance.pdf', 'file_type': 'pdf'}, page_content='www.everstudy.co.in  Query: everstudyclasses@gmail.com \n❖

In [24]:
### Convert chunks to Embeddings
texts = [doc.page_content for doc in chunks]
embeddings = embedding_manager.generate_embedding(texts)    
vectorstore.add_documents(chunks, embeddings)   

Generating embeddings for 3139 texts
Added 3139 documents to vector store. Total now: 0
Successfully added 3139 documents to vector store. Total now: 3139


### RAG Retriever pipeline from VectorStore

In [49]:
class RAGRetriever:
    def __init__(self, vector_store: VectorStore, embedding_manager: EmbeddingManager, top_k: int = 5, score_threshold: float = 0.0):
        ### Initialize the RAG Retriever with vector store and embedding manager
        ###  vector_store: Vector store containing document embeddings
        ###  embedding_manager: Manager for generating embeddings
        ###  top_k: Number of top results to retrieve

        self.vector_store = vector_store
        self.embedding_manager = embedding_manager
        self.top_k = top_k
        self.score_threshold = score_threshold

        ### Generate query embedding and retrieve top_k documents
    def retrieve(self, query: str):
        
        print(f'Retrieving documents for query: "{query}"')
        print(f"Top k : {self.top_k}, Score threshold: {self.score_threshold}")
        retrieved_docs = []
        query_embedding = self.embedding_manager.generate_embedding([query])[0]
       
        try:
            results = self.vector_store.collection.query(
               query_embeddings=[query_embedding],
               n_results=self.top_k
            )
        

            
            if results['documents'] and results['documents'][0]:
                ids = results['ids'][0]
                documents = results['documents'][0]
                metadatas = results['metadatas'][0]
                distances = results['distances'][0]
  
                for i, (doc_id, document, metadata, distance) in enumerate(zip(ids, documents, metadatas, distances)):  
                
                    similarity_score = 1 - distance
                    if similarity_score >= self.score_threshold:
                          retrieved_docs.append({
                            'id': doc_id,
                            'document': document,
                            'metadata': metadata,
                            'similarity_score': similarity_score
                          })
                
            
                print(f'Retrieved {len(retrieved_docs)} documents for query: "{query}"')
            else:
                print(f"Some Error found during retrieval")   
             
        except Exception as e:
            print(f"Some Error found during retrieval: {e}")

        return retrieved_docs
    

In [50]:
rag_retriever = RAGRetriever(vector_store=vectorstore, embedding_manager=embedding_manager)
rag_retriever

In [51]:
rag_retriever.retrieve("What are principles of finance?")

Retrieving documents for query: "What are principles of finance?"
Top k : 5, Score threshold: 0.0
Generating embeddings for 1 texts
Retrieved 5 documents for query: "What are principles of finance?"


[{'id': 'doc_759d7282_1029',
  'document': 'economics, depending on student preparation. It provides a solid grounding in the core concepts of financial\ntheory so that business students interested in a major or minor in finance will also be prepared for more\nrigorous upper-level courses. Concepts are further reinforced through applicable connections and practical\ncalculation techniques for more detailed and realistic company scenarios from various industries.\nPedagogical Foundation\nPrinciples of Finance emphasizes financial concepts relevant to people working in a variety of business\nfunctions. To illuminate the meaningful applications and implications of financial ideas, the book incorporates\na unique use-case approach, providing connections among topics, solutions, and real-world problems. This\nmultifaceted framework drives the integration of concepts while maintaining a modular chapter structure.\nTheoretical and practical aspects are presented in a balanced manner, and sele

In [52]:
rag_retriever.retrieve("What are debentures?")

Retrieving documents for query: "What are debentures?"
Top k : 5, Score threshold: 0.0
Generating embeddings for 1 texts
Retrieved 5 documents for query: "What are debentures?"


[{'id': 'doc_4cdda234_7',
  'document': 'company. Though Perpetuity means forever, bonds with maturity above 100 years are also \nconsidered to be perpetual bonds. \n \n❖ Debentures - In layma n’s term, a Debenture is the acknowledgment of the debt the \norganization has taken from the public at large. Debentures are a debt instrument used by \ncompanies and government to issue the loan. The loan is issued to corporates based on their \nreputation at a fixed rate of interest.',
  'metadata': {'content_length': 433,
   'source': '..\\data\\pdf\\Business_Finance.pdf',
   'total_pages': 64,
   'creator': 'Microsoft® Word for Office 365',
   'title': 'Unit I (Business Environment)',
   'file_type': 'pdf',
   'moddate': '2019-02-03T11:33:09+05:30',
   'author': 'erstudy Classs',
   'page': 4,
   'creationdate': '2019-02-03T11:33:09+05:30',
   'source_file': 'Business_Finance.pdf',
   'page_label': '5',
   'producer': 'Microsoft® Word for Office 365'},
  'similarity_score': 0.469060599803924